Weather dataset

Questions: Where is it hottest? dryest? windiest? during the summer
Looking only at the continental US

In [1]:
import altair as alt
import folium
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

from datetime import datetime
from vega_datasets import data

In [2]:
weather = pd.read_csv('weather.csv')

Where are the weather stations?

In [3]:
stations = weather.groupby(['station', 'latitude', 'longitude']).count().reset_index()

In [4]:
m = folium.Map(location=[40, -100], zoom_start=1)
for i in range(0, len(stations)):
    folium.Marker([stations['latitude'].iloc[i], stations['longitude'].iloc[i]]).add_to(m)
m

Delete stations that are not in the contiguous 48 states.

In [5]:
subdata = weather[~weather['state'].isin(['AB', 'AK', 'BC', 'GU', 'HI', 'MP', 'MB', 'NB', 'NL', 'NS', 'NT', 'ON', 'PE', 'PR', 'QC', 'VI'])]

In [6]:
stations = subdata.groupby(['station', 'latitude', 'longitude']).count().reset_index()
m = folium.Map(location=[40, -100], zoom_start=4)
for i in range(0, len(stations)):
    folium.Marker([stations['latitude'].iloc[i], stations['longitude'].iloc[i]]).add_to(m)
m

Sanity check: Loof for data that are too big / too small

In [7]:
subdata.min()

station      ABERDEEN
state              AL
latitude       24.555
longitude    -124.555
elevation       -36.0
date         20170101
TMIN           -98.86
TMAX           -10.84
TAVG           -20.56
AWND              0.0
WDF5              2.0
WSF5         4.026492
SNOW              0.0
SNWD              0.0
PRCP              0.0
dtype: object

-98.86 seems low. Let us at rows with small values of TMIN.

In [8]:
subdata.loc[subdata.TMIN < -50]

station state  latitude  longitude  elevation      date  \
91571   DECATUR PRYOR FLD    AL   34.6525   -86.9453      180.4  20170804   
148276          ALTUS AFB    OK   34.3622   -98.9761      386.2  20170915   
154693  MAYPORT PILOT STN    FL   30.4000   -81.4167        4.9  20170517   
154694  MAYPORT PILOT STN    FL   30.4000   -81.4167        4.9  20170518   
168315  MAYPORT PILOT STN    FL   30.4000   -81.4167        4.9  20170516   

         TMIN   TMAX  TAVG       AWND   WDF5       WSF5  SNOW  SNWD  PRCP  
91571  -71.86  87.98   NaN   6.039738  240.0  16.105968   0.0   0.0   0.0  
148276 -98.86  96.08   NaN  13.869028  160.0  29.974996   0.0   0.0   0.0  
154693 -70.78  86.00   NaN  13.869028  150.0  27.066974   NaN   NaN   0.0  
154694 -79.78  84.02   NaN  12.750558  150.0  23.935258   NaN   NaN   0.0  
168315 -50.80  80.06   NaN   9.171454  130.0  23.040482   NaN   NaN   0.0

Probably an error (bad sign?). Replace by NaN.

In [9]:
subdata.at[subdata['TMIN'] < -50, 'TMIN'] = np.NaN

/opt/anaconda3/envs/cse512/lib/python3.9/site-packages/pandas/core/indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


In [10]:
subdata.max()

station      Younts Peak
state                 WY
latitude           48.98
longitude       -67.7928
elevation         3541.8
date            20170921
TMIN               98.96
TMAX              129.92
TAVG              105.26
AWND          112.518082
WDF5               360.0
WSF5           180.07367
SNOW           67.992163
SNWD          280.000151
PRCP            26.03151
dtype: object

112 mph on average is tto big?

In [198]:
subdata.loc[subdata.AWND > 70]

station state  latitude  longitude  elevation       date  \
185713   PINE RIDGE AP    SD   43.0206  -102.5183      999.1 2017-08-30   
236985      Lake Irene    CO   40.4100  -105.8200     3261.4 2017-02-15   
236986      Lake Irene    CO   40.4100  -105.8200     3261.4 2017-02-16   
237044      Lake Irene    CO   40.4100  -105.8200     3261.4 2017-04-15   
237045      Lake Irene    CO   40.4100  -105.8200     3261.4 2017-04-16   
...                ...   ...       ...        ...        ...        ...   
264252  El Diente Peak    CO   37.7900  -108.0200     3048.0 2017-05-01   
264253  El Diente Peak    CO   37.7900  -108.0200     3048.0 2017-05-02   
264254  El Diente Peak    CO   37.7900  -108.0200     3048.0 2017-05-03   
264255  El Diente Peak    CO   37.7900  -108.0200     3048.0 2017-05-04   
264256  El Diente Peak    CO   37.7900  -108.0200     3048.0 2017-05-05   

         TMIN   TMAX   TAVG        AWND  WDF5       WSF5  SNOW       SNWD  \
185713  98.96  98.96    NaN   99.096442  99.0  99.096442   NaN        NaN   
236985  10.04  36.50  21.56   72.253162   NaN        NaN   NaN  77.992168   
236986  14.90  43.88  28.22   72.700550   NaN        NaN   NaN  75.984293   
237044  25.16  44.60  34.16   73.147938   NaN        NaN   NaN  62.992160   
237045  28.22  46.94  36.32   70.910998   NaN        NaN   NaN  60.984285   
...       ...    ...    ...         ...   ...        ...   ...        ...   
264252  28.58  46.94  37.58   93.951480   NaN        NaN   NaN  22.992138   
264253  24.80  51.62  39.02   88.135436   NaN        NaN   NaN  22.007886   
264254  27.86  51.44  40.82  105.359874   NaN        NaN   NaN  20.000011   
264255  27.32  60.80  44.78   79.411370   NaN        NaN   NaN  17.992136   
264256  32.36  61.16  46.76   75.832266   NaN        NaN   NaN  15.984261   

        PRCP  
185713   0.0  
236985   0.0  
236986   0.0  
237044   0.0  
237045   0.0  
...      ...  
264252   0.0  
264253   0.0  
264254   0.0  
264255   0.0  
264256   0.0  

[790 rows x 15 columns]

In [199]:
subdata.at[subdata['AWND'] > 70, 'AWND'] = np.NaN

/opt/anaconda3/envs/cse512/lib/python3.9/site-packages/pandas/core/indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


Transforming column to get the date

In [11]:
date = pd.to_datetime(subdata['date'], format='%Y%m%d')

In [12]:
subdata['date'] = date

<ipython-input-12-a0ee75642a13>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subdata['date'] = date


Select summer time

In [13]:
summer = subdata.loc[(date >= datetime(2017, 6, 21)) & (date <= datetime(2017, 9, 20))]

In [42]:
len(summer)

134525

In [41]:
summer.isna().sum()

station          0
state            0
latitude         0
longitude        0
elevation        0
date             0
TMIN           776
TMAX           763
TAVG         51927
AWND         59090
WDF5         61834
WSF5         61800
SNOW         90714
SNWD         31739
PRCP          1403
dtype: int64

Get background map of USA for plotting

In [14]:
usa = data.us_10m.url

Minimum temperatire during summer

In [15]:
Tmin = summer.groupby(['station', 'latitude', 'longitude']).agg({'TMIN': 'min'}).reset_index()

In [27]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='Minimum temperature in summer').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(Tmin).mark_circle(size=15).encode(
        latitude='latitude:Q',
        longitude='longitude:Q',
        color=alt.Color('TMIN:Q', scale=alt.Scale(domain=[0, 80], clamp=True, scheme='plasma'),
        legend=alt.Legend(title='Temperature (F)'))
    )
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

Maximum temperature during summer

In [28]:
Tmax = summer.groupby(['station', 'latitude', 'longitude']).agg({'TMAX': 'max'}).reset_index()

In [29]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='Maximum temperature in summer').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(Tmax).mark_circle(size=15).encode(
        latitude='latitude:Q',
        longitude='longitude:Q',
        color=alt.Color('TMAX:Q', scale=alt.Scale(domain=[65, 130], clamp=True, scheme='plasma'),
        legend=alt.Legend(title='Temperature (F)'))
    )
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

Average temperature during summer

In [30]:
Tavg = summer.groupby(['station', 'latitude', 'longitude']).agg({'TAVG': 'mean'}).reset_index()

In [31]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='Average temperature in summer').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(Tavg).mark_circle(size=15).encode(
        latitude='latitude:Q',
        longitude='longitude:Q',
        color=alt.Color('TAVG:Q', scale=alt.Scale(domain=[45, 100], clamp=True, scheme='plasma'),
        legend=alt.Legend(title='Temperature (F)'))
    )
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

Days of canicule: When the temperature does not get cool during the night. How many days is minimum temperature higher than 70?

In [34]:
canicule = summer.loc[summer['TMIN'] >= 70]

In [35]:
canicule = canicule.groupby(['station', 'latitude', 'longitude', 'state']).agg({'TMIN': 'count'}).reset_index()

In [39]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='Number of days of canicule in summer').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(canicule).mark_circle(size=15).encode(
        latitude='latitude:Q',
        longitude='longitude:Q',
        color=alt.Color('TMIN:Q', scale=alt.Scale(domain=[0, 90], clamp=True, scheme='plasma'),
        legend=alt.Legend(title='Days'))
    )
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

Let us now look at pluviosity. What are the driest parts of the USA?

In [43]:
rain = summer.groupby(['station', 'latitude', 'longitude']).agg({'PRCP': 'sum'}).reset_index()

In [50]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='Precipitation during summer').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(rain).mark_circle(size=15).encode(
        latitude='latitude:Q',
        longitude='longitude:Q',
        color=alt.Color('PRCP:Q', scale=alt.Scale(domain=[0, 20], clamp=True, scheme='plasma'),
        legend=alt.Legend(title='Precipitation (in)'))
    )
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

How well temperature and precipitation correlate?

In [87]:
both = summer.groupby(['station', 'latitude', 'longitude']).agg({'PRCP': 'sum', 'TMIN': 'mean'}).reset_index()

In [93]:
both.max()

station      Younts Peak
latitude           48.98
longitude       -67.7928
PRCP           66.618146
TMIN           86.533933
dtype: object

In [95]:
alt.Chart(both, title='Are high temperatures correlated with high precipitation?').mark_circle(size=15).encode(
    alt.X('TMIN:Q', title='Minimum temperature (F)', scale=alt.Scale(domain=[30, 90])),
    alt.Y('PRCP:Q', title='Precipitation (in)', scale=alt.Scale(domain=[0, 70]))
).properties(
    width=700,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_axis(titleFontSize=20, labelFontSize=20)

alt.Chart(...)

Longest dry period without rain.

In [51]:
dry = subdata.loc[(subdata.PRCP  == 0) & (subdata.SNOW == 0)]

In [56]:
names = subdata.station.unique()

In [62]:
dry_sta = dry.loc[subdata.station == names[0]].sort_values(by=['date']).reset_index()

In [74]:
dry_sta['date'].diff().iloc[0:10]

0      NaT
1   1 days
2   1 days
3   1 days
4   1 days
5   5 days
6   1 days
7   1 days
8   3 days
9   1 days
Name: date, dtype: timedelta64[ns]

In [69]:
len(dry_sta['date'].iloc[1:])

163

In [70]:
len(dry_sta['date'].iloc[:-1])

163

In [83]:
len(names)

1482

Where have we strong winds (storms and hurricanes)
storms: 39-74 hurricane 74

In [200]:
august24 = subdata.loc[subdata.date == datetime(2017, 8, 24)]

In [201]:
august25 = subdata.loc[subdata.date == datetime(2017, 8, 25)]

In [202]:
august26 = subdata.loc[subdata.date == datetime(2017, 8, 26)]

In [203]:
august27 = subdata.loc[subdata.date == datetime(2017, 8, 27)]

In [204]:
august28 = subdata.loc[subdata.date == datetime(2017, 8, 28)]

In [205]:
august29 = subdata.loc[subdata.date == datetime(2017, 8, 29)]

In [206]:
august30 = subdata.loc[subdata.date == datetime(2017, 8, 30)]

In [207]:
august31 = subdata.loc[subdata.date == datetime(2017, 8, 31)]

In [208]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='August 24 2017').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(august24).mark_circle().encode(
        alt.Latitude('latitude:Q'),
        alt.Longitude('longitude:Q'),
        alt.Size('AWND:Q', scale=alt.Scale(domain=[0, 45]), legend=None),
        alt.Color('AWND:Q', scale=alt.Scale(domain=[0, 45], scheme='turbo'),
        legend=alt.Legend(title='Wind (mph)'))
)
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

In [209]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='August 25 2017').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(august25).mark_circle().encode(
        alt.Latitude('latitude:Q'),
        alt.Longitude('longitude:Q'),
        alt.Size('AWND:Q', scale=alt.Scale(domain=[0, 45]), legend=None),
        alt.Color('AWND:Q', scale=alt.Scale(domain=[0, 45], scheme='turbo'),
        legend=alt.Legend(title='Wind (mph)'))
)
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

In [210]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='August 26 2017').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(august26).mark_circle().encode(
        alt.Latitude('latitude:Q'),
        alt.Longitude('longitude:Q'),
        alt.Size('AWND:Q', scale=alt.Scale(domain=[0, 45]), legend=None),
        alt.Color('AWND:Q', scale=alt.Scale(domain=[0, 45], scheme='turbo'),
        legend=alt.Legend(title='Wind (mph)'))
)
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

In [211]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='August 27 2017').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(august27).mark_circle().encode(
        alt.Latitude('latitude:Q'),
        alt.Longitude('longitude:Q'),
        alt.Size('AWND:Q', scale=alt.Scale(domain=[0, 45]), legend=None),
        alt.Color('AWND:Q', scale=alt.Scale(domain=[0, 45], scheme='turbo'),
        legend=alt.Legend(title='Wind (mph)'))
)
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

In [212]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='August 28 2017').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(august28).mark_circle().encode(
        alt.Latitude('latitude:Q'),
        alt.Longitude('longitude:Q'),
        alt.Size('AWND:Q', scale=alt.Scale(domain=[0, 45]), legend=None),
        alt.Color('AWND:Q', scale=alt.Scale(domain=[0, 45], scheme='turbo'),
        legend=alt.Legend(title='Wind (mph)'))
)
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

In [213]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='August 29 2017').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(august29).mark_circle().encode(
        alt.Latitude('latitude:Q'),
        alt.Longitude('longitude:Q'),
        alt.Size('AWND:Q', scale=alt.Scale(domain=[0, 45]), legend=None),
        alt.Color('AWND:Q', scale=alt.Scale(domain=[0, 45], scheme='turbo'),
        legend=alt.Legend(title='Wind (mph)'))
)
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

In [214]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='August 30 2017').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(august30).mark_circle().encode(
        alt.Latitude('latitude:Q'),
        alt.Longitude('longitude:Q'),
        alt.Size('AWND:Q', scale=alt.Scale(domain=[0, 45]), legend=None),
        alt.Color('AWND:Q', scale=alt.Scale(domain=[0, 45], scheme='turbo'),
        legend=alt.Legend(title='Wind (mph)'))
)
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)

In [215]:
alt.layer(
    alt.Chart(alt.topo_feature(usa, 'states'), title='August 31 2017').mark_geoshape(
        fill='#ddd', stroke='#fff', strokeWidth=1
    ),
    alt.Chart(august31).mark_circle().encode(
        alt.Latitude('latitude:Q'),
        alt.Longitude('longitude:Q'),
        alt.Size('AWND:Q', scale=alt.Scale(domain=[0, 45]), legend=None),
        alt.Color('AWND:Q', scale=alt.Scale(domain=[0, 45], scheme='turbo'),
        legend=alt.Legend(title='Wind (mph)'))
)
).project(
    type='albersUsa'
).properties(
    width=750,
    height=500
).configure_view(
    stroke=None
).configure_title(fontSize=24, anchor="middle").configure_legend(titleFontSize=20, labelFontSize=20)

alt.LayerChart(...)